# CALGARY TRAFFIC INCIDENTS DATA ANALYSIS


** **
** **
### DATA 601: Fall 2019 



#### By: Ryan Leeson , Gaurav Kumar, Shora Dehkordi
** **
** **

In [39]:
# the following code will toggle the code for each section makes it easier to present
from IPython.display import HTML
HTML('''<script>
code_show=true; 
function code_toggle() {
 if (code_show){
 $('div.input').hide();
 } else {
 $('div.input').show();
 }
 code_show = !code_show
} 
$( document ).ready(code_toggle);
</script>
The raw code for this IPython notebook is by default hidden for easier reading.
To toggle on/off the raw code, click <a href="javascript:code_toggle()">here</a>.''')

## Introduction
Everyday, one thing every Calgarian must contend with is traffic. Most days traffic simply involves vehicles travelling from points A to B, and having minimal interaction with others. However, in some cases traffic can involve slow vehilce flows as a result of an accident. The focus of this study was to find any trends associated with the reported taffic accidents. This included examining accidents over time of examining the locations of accidents in the City of Calgary. 

The purpose is to provide a visual aid to information Calgarians about trends in traffic accidents in Caglary. From the study, citizens can use the visuals to help plan their daily commutes and be more prepared to respond in case of any accidents. From the study, citizens can use the visuals to help plan their daily commutes and be more prepared to respond in case of any incidents they may encounter. Also, local authorities can address the issues by allocating more resources and take preventive measures to address the frequency of different accidents. Some of the main concerns of the study include what is the most common type of traffic incident in Calgary, which areas in Calgary have the most traffic incidents and how traffic incidents patterns have changed over time



## Data Set
The data set of interest is under the domain of City of Calgary domain. The domain provides a live archive of traffic incidents within Calgary from December 6, 2016 to present and is updated every 10 minutes. The data was obtained from the Open Calgary public data portal and provides tabular structured data about the traffic incidents in Calgary. Permission to use the data is obtained through obliging the terms of use under this license https://data.calgary.ca/d/Open-Data-Terms/u45n-7awa.
The data set format provides information mainly about the traffic incident type, date, and location. “Incident Info” column provides the approximate location as to where the incident occurred, these locations are also tabulated in the “Location” column in the form of longitude and latitude coordinates to indicate the center point. 
 “Description” column describes the type of the incident including multi Vehicle, two vehicle, single vehicle and, pedestrian involvement. 
Date/time of the incident is described in the “Start_DT” and “Modified_DT” columns. The quadrant of where the incident occurred is listed in the “Quadrant” column. (Open Calgary, 2019, online)


## Guiding Questions
The guiding questions proposed for the study were generated with the generalization that a resident or the police will find the data useful for their own purposes. In respect to residents, the visuals may aid in their decision about choosing the route of their everyday commute and take proper cautionary measures by learning what kind of incidents have frequently happened along their commute routes. Alternatively, police may find the data useful in preventing the incidents by studying the trends of areas with denser incidents and the change in incident rates over time.





#### 1.	What is the most common type of accidents in Calgary? 
Studying the most common type of incident may help the drivers be more cautious while driving to minimize the risk of being involved in this type of incident. 

#### 2.	What is the trend of  type of accidents in each month?
If there is a trend with the incidents and certain time periods, then it may benefit the City of Calgary to study the trend of incidents over time. If incident rates increase during the snow season or during rush hour, then the City of Calgary may want to allow further resources during that time period to alleviate the issue or change the traffic pattern.

#### 3.	How are traffic accidents distributed throughout the city?
Presenting the pattern by location over a 4-year period helps drivers get a grasp of driving risks en route to their  destination and allows police and the City of Calgary to allocate resources to those locations.

#### 4.	Where are accidents occurring throughout the city?
The location of the most frequent incident might give the drivers and the City of Calgary an insight into what might be the cause and help them mitigate that using preventive measures. 

#### 5.	Are there locations where  accidents happen more frequently?
Presenting the clustering of certain incident types may prepare drivers, police and the City of Calgary to better respond to the upcoming incidents. It might be beneficial for the city to study the clustered locations where the most common type of incident happens and address the issue by planning some constructive modifications to the route or traffic pattern 


In [19]:
import numpy as np
import pandas as pd
import geopandas as gpd
import shapely.geometry as sg

import matplotlib as mpl
import matplotlib.pyplot as plt

import plotly as plotly
import plotly.offline as py
import plotly.graph_objs as go
import plotly.express as px
import re
import warnings
warnings.filterwarnings('ignore')

from sklearn.cluster import KMeans
from scipy.spatial import Voronoi, voronoi_plot_2d
from scipy import stats

py.init_notebook_mode(connected=True)

#%matplotlib inline
mpl.rcParams['figure.dpi']= 96
mpl.style.use('ggplot')

In [8]:
rdata = pd.read_csv("./Traffic_Incidents.csv")
display(' Raw Data ', rdata.head())


' Raw Data '

INCIDENT INFO  \
0   Northbound Deerfoot Trail approaching 64 Aven...   
1                  Shepard Road and Barlow Trail SE    
2    Eastbound Glenmore Trail and Deerfoot Trail SE    
3        Northbound Deerfoot Trail and 64 Avenue NE    
4                Taradale Drive and Tarington Wy NE    

                                       DESCRIPTION                START_DT  \
0   Multi-vehicle incident. Blocking the left lane  10/12/2019 05:45:40 PM   
1                         Single vehicle incident.  10/12/2019 05:21:10 PM   
2  Multi-vehicle incident. Blocking the right lane  10/12/2019 05:00:53 PM   
3                          Multi-vehicle incident.  10/12/2019 04:22:53 PM   
4     There is an incident involving a pedestrian.  10/12/2019 04:03:48 PM   

  MODIFIED_DT QUADRANT   Longitude   Latitude  \
0         NaN      NaN -114.046044  51.104815   
1         NaN      NaN -113.984294  50.965172   
2         NaN      NaN -114.039335  50.993965   
3         NaN      NaN -114.046072  51.104640   
4         NaN      NaN -113.927790  51.114012   

                                    location  Count  \
0   (51.10481536305839, -114.04604369289085)      1   
1   (50.96517240002418, -113.98429427871812)      1   
2  (50.993965227644814, -114.03933531877112)      1   
3   (51.10464014377781, -114.04607207692446)      1   
4  (51.114012012562895, -113.92778979143233)      1   

                                                  id  
0  2019-10-12T17:45:4051.10481536305839-114.04604...  
1  2019-10-12T17:21:1050.96517240002418-113.98429...  
2  2019-10-12T17:00:5350.993965227644814-114.0393...  
3  2019-10-12T16:22:5351.10464014377781-114.04607...  
4  2019-10-12T16:03:4851.114012012562895-113.9277...

# Data Wrangling

We encountered some missing data for the quadrant which could be obtained from the Incident Info column and also needed to extract type of each incident from the Description column. 
Although the data set description suggests the period of data acquisition is 2016 to 2019, the data wrangling phase has revealed that the time periods for which data is completely availble are as follows.  
- 2016: Only December
- 2017: All months except January
- 2018: Complete
- 2019: Complete till May 31 ( July and August are missing. September and October are incomplete)

Our cleaning and wrangling activities included:

1. Timestamp data conversion:
    We have converted the Timestamp provided in the "START_DT column to datetime object and extracted Year, Month,Day and Time  
2. Text Processing:
   We have created a robust text processing section using regular expressions in order to extract useful information such   as types of the incidents from the DESCRIPTION column. We have to take care of all possible ways in which user might have entered data for example two vehicle can also be written as 2 vehicle

3. After using the dataset we realize that Quadrant informartion provided in this dataset is not aligned with the co-ordinate information provided. As we wanted to do the analysis of traffic accident based on Quadrant as well so we have to fill this gap of inconsistent data.  We took an approach to read the address provided in the INCIDENT INFO column and identify its quadrant. Although there are some data point which donot have the complete address as well but with our approach of reading the address we are able to fill most of the data with correct quadrant.

4. Deleting of rows and columns:
    -The ID column is a unique identifier of each row which does not provide any information.
    -LOCATION Column includes the longitude and Latitude which are available in LON and LAT columns. 
    -INCIDENT INFO, DESCRPTION, START_DT and MODIFIED_DT columns have been deleted after extracting required information
    -All rows with missing quadrant or type information have been deleted
    
5. Manipulating data frame:
    Organize the data frames grouped by type, Year, hour or quadrant to generate respective visualizations.


In [9]:
# Added LON, LAT, INCIDENT INFO and QUADRANT Columns in order to plot the maps & extract the quadrant 
# from the Incident Info column for those rows with missing quadrant

rdata['START_DT'] = pd.to_datetime(rdata['START_DT'], format= "%m/%d/%Y %I:%M:%S %p")
rdata['DATE'] = rdata.START_DT.dt.date
rdata['DAY'] = rdata.START_DT.dt.day
rdata['MONTH'] = rdata.START_DT.dt.month
rdata['YEAR'] = rdata.START_DT.dt.year
rdata['MONTHNAME'] = rdata.START_DT.dt.strftime("%B %Y")
rdata['HOUR'] = rdata.START_DT.dt.hour
rdata['MINUTE'] = rdata.START_DT.dt.minute


sampleData = pd.DataFrame({'ADDRESS' : rdata['INCIDENT INFO'], 'DESCRIPTION' : rdata.DESCRIPTION, 
                           'COUNT' : rdata.Count, 'LON' : rdata.Longitude, 
                           'LAT' : rdata.Latitude, 'QUADRANT': rdata.QUADRANT,
                           'YEAR':rdata.YEAR,'MONTH':rdata.MONTH,
                           'MONTHNAME' :rdata.MONTHNAME,
                           'DAY':rdata['DAY'], 'HOUR':rdata.HOUR })
#REGEX
sampleData.DESCRIPTION = sampleData.DESCRIPTION.str.lower()
sampleData.ADDRESS = sampleData.ADDRESS.str.lower()

# Function to returns true if there is a positive search else false
def checkSubStr(text, *words):
    initialPattern =""
    conditionalOr=""
    for x in words:
        initialPattern += conditionalOr+".*" + x + ".*"
        conditionalOr ="|"
    pattern = re.compile(initialPattern, re.IGNORECASE)
    result = pattern.search(str(text)) is not None
    return result

#Function returns the quadrant key after searching the text
def fillMissingQuadrant(text):
    region = [' nw', ' ne', ' sw', ' se']
    for x in region:
        pattern = re.compile(".*" + x + ".*", re.IGNORECASE)
        result = pattern.match(str(text)) is not None
        if result:
            return x.upper().strip()
    return "BR"

#Update the quadrant information from address
sampleData.QUADRANT.update( sampleData.ADDRESS.apply(fillMissingQuadrant))

# Identify different of accident by processing the Description text
single_vehicle = sampleData.DESCRIPTION.apply(checkSubStr, args = (["single vehicle"]))
two_vehicle = sampleData.DESCRIPTION.apply(checkSubStr, args = (["two vehicle","2 vehicle"]))
multi_vehicle = sampleData.DESCRIPTION.apply(checkSubStr, args = (["multi vehicle","multi-vehicle"]))
pedestrian = sampleData.DESCRIPTION.apply(checkSubStr, args = (["pedestrian"]))

incidents_df = pd.DataFrame({
                            'ADDRESS' : sampleData.ADDRESS,
                            'DESCRIPTION' : sampleData.DESCRIPTION,
                            'COUNT' : sampleData.COUNT,
                            'PEDESTRIAN':pedestrian,
                            'SINGLE_VEHICLE':single_vehicle,
                            'TWO_VEHICLE' : two_vehicle,  
                            'MULTI_VEHICLE': multi_vehicle,
                            'LON': sampleData.LON,
                            'LAT': sampleData.LAT,
                            'YEAR': sampleData.YEAR,
                            'MONTH': sampleData.MONTH,
                            'MONTHNAME' : sampleData.MONTHNAME,
                            'DAY': sampleData.DAY,
                            'HOUR': sampleData.HOUR,
                            'QUADRANT' : sampleData.QUADRANT,

                            })


Type = len(incidents_df) * [0]
for row1 in range(len(incidents_df)):
    for col1 in incidents_df.columns[3:7]:
        if incidents_df.loc[row1,col1] == True:
            Type[row1] = col1
            

incidents_df['TYPE'] = Type
incidents_df['TYPE'].replace(to_replace = 0, value=np.NaN, inplace=True) # Replace all missing Types with NaN
# incidents_df['REGION'].replace(to_replace = 0, value=np.NaN, inplace=True) # Replace all missing Quadrant with NaN

# Create a master cleaned dataframe 
inc_type_df = pd.DataFrame({
                            'YEAR': incidents_df.YEAR,
                            'MONTH': incidents_df.MONTH,
                            'DAY': incidents_df.DAY,
                            'HOUR': incidents_df.HOUR,
                            'TYPE' : incidents_df.TYPE,
                            'QUADRANT' : incidents_df.QUADRANT,
                            'ADDRESS' : incidents_df.ADDRESS,
                            'LON': incidents_df.LON,
                            'LAT': incidents_df.LAT,
                            'COUNT' : incidents_df.COUNT,
                            'MONTHNAME': incidents_df.MONTHNAME

                            })

inc_type_df=inc_type_df[~inc_type_df['MONTHNAME'].isin(['October 2019','September 2019', 'June 2019'])].dropna()
display("Cleaned Data", inc_type_df.head())



'Cleaned Data'

YEAR  MONTH  DAY  HOUR            TYPE QUADRANT  \
833  2019      5   31    23  SINGLE_VEHICLE       SE   
834  2019      5   31    17     TWO_VEHICLE       SE   
835  2019      5   31    17     TWO_VEHICLE       SW   
836  2019      5   31    16     TWO_VEHICLE       SE   
837  2019      5   31    16  SINGLE_VEHICLE       NE   

                                               ADDRESS         LON        LAT  \
833   eastbound memorial drive approaching barlow t... -114.002064  51.043449   
834     eastbound anderson road and deerfoot trail se  -114.033912  50.948342   
835                        1a street and 52 avenue sw  -114.067139  51.007163   
836    eastbound memorial drive and deerfoot trail se  -114.019434  51.048860   
837             northbound 52 street and 16 avenue ne  -113.958281  51.065795   

     COUNT MONTHNAME  
833      1  May 2019  
834      1  May 2019  
835      1  May 2019  
836      1  May 2019  
837      1  May 2019

## What is the most common type of accidents in Calgary?

In [10]:
Most_common_type = inc_type_df[['TYPE', 'COUNT'] ].groupby(['TYPE']).sum().sort_values(by = 'COUNT', ascending = False).reset_index()
#display("Most Common Type of Incident", Most_common_type)
labels = ['Two Vehicle','Single Vehicle','Multi Vehicle','Pedestrian']
fig = go.Figure(
    data=[go.Bar(
            x=labels, 
            y=Most_common_type.COUNT,
            text=Most_common_type.COUNT,
            textposition='outside'
        )],
    layout=go.Layout(
        title='Total Accident Count by Type in Last Three Year',
        xaxis=dict(showgrid=False, zeroline=False),
        yaxis=dict(showgrid=False, zeroline=False,showticklabels=False),
    )
               )
fig.show()

values = Most_common_type.COUNT

fig1 = go.Figure(data=[go.Pie(labels=labels, values=values)],
                layout=go.Layout(
                            title='Total accident proportion by type in last three year'
    ))
fig1.show()

The plot shows that, from December 2016, two vehicle accidents make up the largest proportion of reported incidents in Calgary. Also, Pedestrian related incidents make out the smallest proportion. 

From the counts, of the different types of accidents, two vehivle accidents make up the majority of the overall number of traffic accidents that have occurred in Calgary. Comparatively, pedestrian related incidents only make up approximately 3% of the accidents that occurred.  

## What is the trend of the accidents in each month?

The following table shows total number of two-vehicle incidents for each year. However, due to incomplete annual data for 2016,2017 and 2019, only 2018 count is representative of a true count. 


In [35]:
Most_common_type_Ytrend = inc_type_df[['YEAR','MONTH','MONTHNAME','TYPE', 'COUNT']].groupby(
    ['YEAR','MONTH','MONTHNAME','TYPE']).sum().reset_index()

monthly_two_inc_df = Most_common_type_Ytrend[Most_common_type_Ytrend.TYPE == 'TWO_VEHICLE']
monthly_inc_total_l = list(Most_common_type_Ytrend.groupby(['YEAR','MONTH']).sum().reset_index().COUNT)

monthly_inc_two_l = list(monthly_two_inc_df.COUNT)
monthly_inc_ped_l = list(Most_common_type_Ytrend[Most_common_type_Ytrend.TYPE == 'PEDESTRIAN'].COUNT)
monthly_inc_sin_l = list(Most_common_type_Ytrend[Most_common_type_Ytrend.TYPE == 'SINGLE_VEHICLE'].COUNT)
monthly_inc_mul_l = list(Most_common_type_Ytrend[Most_common_type_Ytrend.TYPE == 'MULTI_VEHICLE'].COUNT)

prop_two_inc = pd.Series([(x/y)*100 for x,y in zip(monthly_inc_two_l, monthly_inc_total_l)])
prop_ped_inc = pd.Series([(x/y)*100 for x,y in zip(monthly_inc_ped_l, monthly_inc_total_l)])
prop_sin_inc = pd.Series([(x/y)*100 for x,y in zip(monthly_inc_sin_l, monthly_inc_total_l)])
prop_mul_inc = pd.Series([(x/y)*100 for x,y in zip(monthly_inc_mul_l, monthly_inc_total_l)])

monthly_inc_df = pd.DataFrame({'YEAR': list(monthly_two_inc_df.YEAR.astype(str)) ,
                                   'MONTH': list(monthly_two_inc_df.MONTH),
                                   'MONTHNAME': list(monthly_two_inc_df.MONTHNAME),
                                   'COUNT': list(monthly_two_inc_df.COUNT),
                                   'PROPTWO':prop_two_inc,
                                   'PROPPED': prop_ped_inc,
                                   'PROPSIN': prop_sin_inc,
                                   'PROPMUL': prop_mul_inc,
                                   'TOTAL': monthly_inc_total_l})
fig1 = px.line(monthly_inc_df, x="MONTHNAME", y="TOTAL",   title="Total Number of Accidents")
fig1.show()



In [38]:
incTypeKey = ['SINGLE_VEHICLE', 'TWO_VEHICLE','MULTI_VEHICLE','PEDESTRIAN']
incTypeName =[ 'Single Vehicle', 'Two Vehicle', 'Multi Vehicle','Pedestrian']

#Function is used to create total count and type of accident plot
def showTypeTrend(typeKey, typeName):
    
    monthly_two_inc_df = Most_common_type_Ytrend[Most_common_type_Ytrend.TYPE == typeKey]
    monthly_inc_two_l = list(monthly_two_inc_df.COUNT)
    monthly_inc_total_l = list(Most_common_type_Ytrend.groupby(['YEAR','MONTH']).sum().reset_index().COUNT)
    prop_two_inc = pd.Series([(x/y)*100 for x,y in zip(monthly_inc_two_l,monthly_inc_total_l)])
    monthly_two_inc_df = pd.DataFrame({'YEAR': list(monthly_two_inc_df.YEAR.astype(str)) ,
                                       'MONTH': list(monthly_two_inc_df.MONTH),
                                       'MONTHNAME': list(monthly_two_inc_df.MONTHNAME),
                                       'COUNT': list(monthly_two_inc_df.COUNT),
                                       'PROPORTION':prop_two_inc})

    fig3 = go.Figure(layout=go.Layout(
            title='Total Number of '+ typeName +' Accident',
        ))
    def addTraceYear(year):
        filter_year=monthly_two_inc_df[monthly_two_inc_df.YEAR == year]
        fig3.add_trace(go.Bar(
                    x= filter_year.MONTHNAME , 
                    y=filter_year.COUNT,
                    name= year,
                    width =0.2
                ))
    yearList= ['2016','2017','2018','2019']
    for x in yearList:
        addTraceYear(x)
    fig3.show()

for x in range(0,4):
    showTypeTrend(incTypeKey[x], incTypeName[x])



In [34]:
fig2 = go.Figure(layout=go.Layout(
            title='Percentage of all type of Accident',
            xaxis=dict(title_text=''),
            yaxis=dict(title_text='Percentage'),
        ))
fig2.add_trace(go.Scatter(x=monthly_inc_df.MONTHNAME , y=monthly_inc_df.PROPPED,
                    mode='lines',name='Pedestrian'))
fig2.add_trace(go.Scatter(x=monthly_inc_df.MONTHNAME , y=monthly_inc_df.PROPSIN,
                    mode='lines',name='Single Vehicle'))
fig2.add_trace(go.Scatter(x=monthly_inc_df.MONTHNAME , y=monthly_inc_df.PROPTWO,
                    mode='lines', name='Two Vehicle'))
fig2.add_trace(go.Scatter(x=monthly_inc_df.MONTHNAME , y=monthly_inc_df.PROPMUL,
                    mode='lines', name='Multi Vehicle'))

fig2.show()

We can see from the Single Vehicle Accident plot that there is more accident in the snow season and similar trend is observed in the Two vehicle accident with relatively more accident in the summer season. Multi Vehicle Accident is more on the snow season and have similar trend as per Single Vehicle Accident as seen in the above plot.

 

Pedestrian Accident follows the general trend that there is more Accident in the snow season but we also see from the above plot that there is a spike in the Pedestrian Accident when season changes.

 

Looking the proportions of the types of accidents on a month by month basis, the proportions of pedestrian involved and multi-vehicle accidents do not change over time.

 

The overall accident proportion is dominated by Single Vehicle and Two Vehicle Incident and we can also observe that in the month of April and May there is an increase in percentage of Two Vehicle Accident and dip for the Single Vehicle Accident.

 

Looking at the proportion of single vehicle accidents, there appears to be a trend where a higher proportion of accidents occurs during months such as December and February. This proportion tends to decrease as we move into the spring, but increases again in the summer.

 

Overall, it is the number of single vehicle influences the change in the proportion of two vehicle accidents that occurs.

Looking the proportions of the types of accidents on a month by month basis, the proportions of pedestrian involved and multi-vehicle accidents do not chnage over time. 

Looking at the proportion of single vehicle accidents, there appears to be a trend where a higher proportion of accidents occurs during months such as December and February. This proportion tends to decrease as we move into the spring, but increases again in the summer. 

Overall, it is the number of single vehicle influences the change in the proportion of two vehicle accidents that occurs.

In [20]:
rushhour = inc_type_df['HOUR'].isin ([7,8,15,16,17])
inc_type_df['HOURTYPE']= np.where(rushhour, 'Rush Hour','Not Rush Hour')
#inc_type_df
n_rushhour = len(inc_type_df[inc_type_df['HOURTYPE'] == 'Rush Hour'])
n_notrushhour = len(inc_type_df[inc_type_df['HOURTYPE'] == 'Not Rush Hour'])
hourtype_df = inc_type_df[['HOURTYPE','TYPE', 'COUNT']].groupby(
    ['TYPE','HOURTYPE']).sum().sort_values(by = 'COUNT', ascending = False).reset_index()

# Calculating proportion of each type of accident for rush hour vs not rush hour
hourtype_df['PROPORTION'] = len(hourtype_df['HOURTYPE'])*[np.nan]
for i in range(0,8):

    if hourtype_df['HOURTYPE'][i] == 'Rush Hour': 
        hourtype_df['PROPORTION'][i] = hourtype_df['COUNT'][i]/n_rushhour
    else: 
        hourtype_df['PROPORTION'][i] = hourtype_df['COUNT'][i]/n_notrushhour


fig = px.bar(hourtype_df, x="HOURTYPE", y="PROPORTION", barmode='group', color='TYPE', labels={'HOURTYPE': '', 
                'PROPORTION' : 'Proportion'}
              , title=' Accident Proportions During Rush Hours vs Not Rush Hours')
fig.show()


This graph shows that proportion of two-vehicle accidents happened during "rush hours" are slightly more  vs. those happened during "not rush hours". This could be simply explained as the increased traffic volume  on the street during the rush hour which might lead to more accidents. 

## How are traffic accidents distributed throughout the city?

In [25]:
inc_locs = pd.DataFrame({"COUNT" : inc_type_df['COUNT'], "LON" : inc_type_df['LON'], "LAT" : inc_type_df['LAT'], 
                         "QUADRANT" : inc_type_df['QUADRANT'], "TYPE" : inc_type_df['TYPE'],
                         "YEAR" : inc_type_df['YEAR']})
inc_locs['LON'] = inc_locs['LON'].astype(float)  # Change type of the object to float
inc_locs['LAT'] = inc_locs['LAT'].astype(float)    # Change type of the object to float

try:
    file = open('mapbox.token', 'r')
    for line in file:
        token = line.rstrip() # Use rstrip to get EOL-free lines
    file.close()
except FileNotFoundError as fnfe:
    print(fnfe)
    
    
data = []
for typ in ['SINGLE_VEHICLE', 'TWO_VEHICLE', 'MULTI_VEHICLE', 'PEDESTRIAN']:
    type_data = dict(
            lat = inc_locs.loc[inc_locs['TYPE'] == typ,'LAT'],
            lon = inc_locs.loc[inc_locs['TYPE'] == typ,'LON'],
            name = typ,
            marker = dict(size = 5),
            type = 'scattermapbox'
        )
    data.append(type_data)
    
    
layout = go.Layout(
    title='Calgary Traffic Accidents<br>Use right mouse button to rotate/pitch<br>Use drop-down menus to filter for type or map style',
    autosize=True,
    height=1024,
    hovermode= "closest",
    mapbox=dict(
        style="streets", # Styles can be one of streets, light, dark, outdoors, satellite
        accesstoken=token,
        bearing=0,
        center=dict(  # These are Calgary coordinates
            lat=51.0486,
            lon=-114.0708
        ),
        pitch=0, # Pitch lets you pitch up or down
        zoom=10
    ),
)

# Add a drop-down menu to select the type of Accident to visualize,


updatemenus=list([
    
# drop-down 1: map styles menu
    # buttons containes as many dictionaries as many alternative map styles I want to offer
    dict(
        buttons=list([
            dict(
                args=['mapbox.style', 'streets'],
                label='Street',
                method='relayout'
            ),
            
            dict(
                args=['mapbox.style', 'dark'],
                label='Dark',
                method='relayout'
            ),                    
            dict(
                args=['mapbox.style', 'light'],
                label='Light',
                method='relayout'
            ),
            
            dict(
                args=['mapbox.style', 'satellite-streets'],
                label='Satellite with Streets',
                method='relayout'
            )                    
        ]),
        # direction where I want the menu to expand when I click on it
        direction = 'down',
      
        # here I specify where I want to place this drop-down on the map
        x = 0.75,
        xanchor = 'left',
        y = 0.96,
        yanchor = 'bottom',
      
        # specify font size and colors
        bgcolor = '#fff7bc',
        bordercolor = '#FFFFFF',
        font = dict(size=13)
    ),    
    
    
    
    dict(
         # for each button I specify which dictionaries of my data list I want to visualize.  I have 4 different
         # types of Accident but I have 5 options: the first will show all of them, while from the second to the last option, only
         # one type at the time will be shown on the map
        
         buttons=list([
             
            dict(label = 'All Types',
                 method = 'update',
                 args = [{'visible': [True, True, True, True]}]),
            dict(label = 'Single-Vehicle',
                 method = 'update',
                 args = [{'visible': [True, False, False, False]}]),
            dict(label = 'Two-Vehicle',
                 method = 'update',
                 args = [{'visible': [False, True, False, False]}]),
             dict(label = 'Multi-Vehicle',
                 method = 'update',
                 args = [{'visible': [False, False, True, False]}]),
             dict(label = 'Pedestrian',
                 method = 'update',
                 args = [{'visible': [False, False, False, True]}]),
             
          
        ]),
        # direction where the drop-down expands when opened
        direction = 'down',
        # positional arguments
        x = 0.01,
        xanchor = 'left',
        y = 0.96,
        yanchor = 'bottom',
        # fonts and border
        bgcolor = '#fff7bc',
        bordercolor = '#FFFFFF',
        font = dict(size=13)
    )

])

# assign the list of dictionaries to the layout dictionary
layout['updatemenus'] = updatemenus

fig = dict(data=data, layout=layout)
py.iplot(fig)



## Where are accidents occurring throughout the city?



In [17]:
Most_common_type_loc = inc_type_df[['QUADRANT','TYPE', 'COUNT']].groupby(
    ['TYPE','QUADRANT']).sum().sort_values(by = 'COUNT', ascending = False).reset_index()

fig = px.bar(Most_common_type_loc, x="QUADRANT", y="COUNT", barmode='group', color='TYPE')
fig.show()

The plot shows a recurring trend when it comes to traffic incidents in Calgary:

- Two vehicle accidents made up the largest proportion of accidents in each quadrant.

- After, single vehicle made up the second largest, followed closely by multi-vehicle and finally pedestrian related.

This trend is the same as the one observed when we look at the city as a whole. 

Another trend is that the South East quandrant shows the highest number of accidents for all accident type, followed by the North East, the South West, and the North West. The only time this pattern is broken is for pedestrian involved accidents where the South West has the highest number of incidents.


Overall the eastern quadrants of Calgary appear to show the most number of incidents, with the south east showing the highest number of incidents.

The BR values represent accidents that occurred on quadrant boundaries, for example, Centre st. As a result they cannot be easily defined as occurring in a quadrant. However, compared to the number of incidents that occur in each quandrant, the number of accidents that occurred on a boundary is small. If they were distributed to a quadrant, it would not affect the trends that have already been observed. 

In [26]:
try:
    file = open('mapbox.token', 'r')
    for line in file:
        token = line.rstrip() # Use rstrip to get EOL-free lines
    file.close()
except FileNotFoundError as fnfe:
    print(fnfe)
    

data = []
for loc in ['NW', 'NE', 'SW',  'SE', 'BR']:
    loc_data = dict(
            lat = inc_locs.query("TYPE == 'TWO_VEHICLE' ").loc[inc_locs['QUADRANT'] == loc,'LAT'],
            lon = inc_locs.query("TYPE == 'TWO_VEHICLE' ").loc[inc_locs['QUADRANT'] == loc,'LON'],
            name = loc,
            marker = dict(size = 5),
            type = 'scattermapbox'
        )
    data.append(loc_data)
    
    
layout = go.Layout(
    title='Calgary Traffic Incidents<br>Use right mouse button to rotate/pitch<br>Use drop-down menu to filter for quadrant',
    autosize=True,
    height=1024,
    hovermode= "closest",
    mapbox=dict(
        style="dark", # Styles can be one of streets, light, dark, outdoors, satellite
        accesstoken=token,
        bearing=0,
        center=dict(  # These are Calgary coordinates
            lat=51.0486,
            lon=-114.0708
        ),
        pitch=0, # Pitch lets you pitch up or down
        zoom=10
    ),
)



updatemenus=list([
    

    dict(
        
         buttons=list([
             
            dict(label = 'All Quadrants',
                 method = 'update',
                 args = [{'visible': [True, True, True, True,True]}]),
             dict(label = 'North West',
                 method = 'update',
                 args = [{'visible': [True, False, False, False,False]}]),
             dict(label = 'North East',
                 method = 'update',
                 args = [{'visible': [False, True, False, False,False]}]),
             dict(label = 'South West',
                 method = 'update',
                 args = [{'visible': [False, False, True, False,False]}]),
             dict(label = 'South East',
                 method = 'update',
                 args = [{'visible': [False, False, False, True,False]}]),
             dict(label = 'Boundaries',
                 method = 'update',
                 args = [{'visible': [False, False, False, False,True]}]),

          
        ]),
        # direction where the drop-down expands when opened
        direction = 'down',
        # positional arguments
        x = 0.01,
        xanchor = 'left',
        y = 0.96,
        yanchor = 'bottom',
        # fonts and border
        bgcolor = '#fff7bc',
        bordercolor = '#FFFFFF',
        font = dict(size=13)
    )

])

# assign the list of dictionaries to the layout dictionary
layout['updatemenus'] = updatemenus

fig = dict(data=data, layout=layout)
py.iplot(fig)



## Are there locations where accidents happen more frequently?
A glance on the scatter map of the Two-vehicle incident shows a cluster of these type of incidents in downtown area

In [30]:
data = []
for typ in ['TWO_VEHICLE', 'MULTI_VEHICLE', 'SINGLE_VEHICLE', 'PEDESTRIAN']:
    type_data = dict (
            lat = inc_locs.loc[inc_locs['TYPE'] == typ,'LAT'],
            lon = inc_locs.loc[inc_locs['TYPE'] == typ,'LON'],
            name = typ,
            reversescale = True,
            radius = 10,
            type = 'densitymapbox'
        )
    data.append(type_data)

    
layout = go.Layout (
    title = 'Density of Calgary traffic incidents by type<br>Use right mouse button to rotate/pitch',
    autosize = True,
    height = 1024,
    hovermode = "closest",
    mapbox = dict(
        style = "streets", # Styles can be one of streets, light, dark, outdoors, satellite
        accesstoken = token,
        bearing = 0,
        center = dict(  # These are Calgary coordinates
            lat = 51.0486,
            lon = -114.0708
        ),
        pitch = 0, # Pitch lets you pitch up or down
        zoom = 10
    ),
)


updatemenus = list ([
    

    dict (
        
         buttons = list ([
             
            dict ( label = 'All Types',
                 method = 'update',
                 args = [{'visible': [True, True, True, True]}]),
            dict ( label = 'Two-Vehicle',
                 method = 'update',
                 args = [{'visible': [True, False, False, False]}]),
            dict ( label = 'Multi-Vehicle',
                 method = 'update',
                 args = [{'visible': [False, True, False, False]}]),
            dict ( label = 'Single-Vehicle',
                 method = 'update',
                 args = [{'visible': [False, False, True, False]}]),
            dict ( label = 'Pedestrian',
                 method = 'update',
                 args = [{'visible': [False, False, False, True]}]),
 
          
        ]),
        # direction where the drop-down expands when opened
        direction = 'down',
        # positional arguments
        x = 0.01,
        xanchor = 'left',
        y = 0.96,
        yanchor = 'bottom',
        # fonts and border
        bgcolor = '#fff7bc',
        bordercolor = '#FFFFFF',
        font = dict ( size = 13)
    )

])

layout['updatemenus'] = updatemenus

fig = dict ( data = data, layout = layout)
py.iplot (fig)

The heatmap indicates that a higher concentration of accidents tends to occur on either roadways or within the downtown city core. It can be absorved that major roadways, such as Deerfoot tr., Crowchild tr., MacLeod tr., etc, show a consistantly high concentration of accidents along their routes. This occurance is 

Another trend that can be observed is consistantly high concentrations of high number of accidents is found the further toward the city centre the travel. This trend would not be inconsistant with typical assumptions. As the city centre, there is a large amount of office and recreational space concentrated in this location. As a result, on a daily basis, there are large volumes the traffic traveling into and out of the city centre. These volumes, and the daily frequency of their occurance, increase the change of the occurance of an accident. So, seeing higher numbers of accidents occurring near the city centre is not an overall surprising observation.

The heatmap also shows a high concentration of accidents occurring at various intersections, especially at exits and entrances to major roads. Many likely have experience with where a lack of coordination or simple pigheadedness  has resulted in issues where merging or traveling through intersections nearly ended dangerously. Because of the interactions that occurs at these locations, joining already flowing traffic or traveling in an alternative direction to traffic, the chance of an accident occurring is high. So, it is not surprising to observe higher numbers of accidents at such locations.

An examination of pedestrian related accidents indicates higher occurance in the city centre. A closer examination of the various occurances of pedestrian related accidents appears to show that they are tend to occur at intersections. 

Two vehicle accidents appear to be evenly distributed throughout the whole of Calgary. From the intensity displayed on the map, two vehicle accidents appear to be very widely distributed over all major road in the city.

Multi-vehicle incidents appear to mostly be concentrated to the larger roadways such as highways. Deerfoot tr., Glenmore tr., the Eastern portion of Highway 1 and Crowchild tr. near the river show the highest occurance of multi-vehicle incidents.

Like two vehicle accidents, single vehicle accidents appear to be very evenly distributed throughout the city. There does not appear to be an area of the city where single vehicle incidents would be more prevalent than others. However, many would appear to be concentrated to large roads as Deerfoot and Glenmore.

In [31]:
#   Examination of occurences of accident over time.

data = []
for yr in [2016, 2017, 2018, 2019]:
    type_data = dict(
            reversescale = True,
            lat = inc_locs.loc[inc_locs['YEAR'] == yr,'LAT'],
            lon = inc_locs.loc[inc_locs['YEAR'] == yr,'LON'],
            name = yr,
            radius = 10,
            type = 'densitymapbox'
        )
    data.append(type_data)
    
    
layout = go.Layout (
    title = 'Density of Calgary traffic accidents by year<br>Use right mouse button to rotate/pitch',
    autosize = True,
    height = 1024,
    hovermode = "closest",
    mapbox = dict(
        style = "streets", # Styles can be one of streets, light, dark, outdoors, satellite
        accesstoken = token,
        bearing = 0,
        center = dict(  # These are Calgary coordinates
            lat = 51.0486,
            lon = -114.0708
        ),
        pitch = 0, # Pitch lets you pitch up or down
        zoom = 10
    ),
)



updatemenus=list([
    

    dict(
        
         buttons=list([
             
            dict(label = 'All Years',
                 method = 'update',
                 args = [{'visible': [True, True, True, True]}]),
            dict(label = '2016',
                 method = 'update',
                 args = [{'visible': [True, False, False, False]}]),
            dict(label = '2017',
                 method = 'update',
                 args = [{'visible': [False, True, False, False]}]),
             dict(label = '2018',
                 method = 'update',
                 args = [{'visible': [False, False, True, False]}]),
             dict(label = '2019',
                 method = 'update',
                 args = [{'visible': [False, False, False, True]}]),
 
          
        ]),
        # direction where the drop-down expands when opened
        direction = 'down',
        # positional arguments
        x = 0.01,
        xanchor = 'left',
        y = 0.96,
        yanchor = 'bottom',
        # fonts and border
        bgcolor = '#fff7bc',
        bordercolor = '#FFFFFF',
        font = dict(size=13)
    )

])

# assign the list of dictionaries to the layout dictionary
layout['updatemenus'] = updatemenus

fig = dict(data=data, layout=layout)
py.iplot(fig)




An examination of the distribution of accidents based on year shows that there is no change in the intensity of occurrances from year to year. The intencity for certain areas may shift year after year, but overall the same locations are consistantly affected by the reoccurrance of accidents year after year. 

The data available for the yaer 2016 is limited to the month of December, however, the locations of a higher intensity for the occurrance of various incidents is consistant with the trends viewed in subsequent years. 

2019 shows a decreased distribution of incidents compared to previous years. There is still a high level of accidents occurring in the city centre. Towards the city limits there is a reduction in the intensity of the density plot indicating a reduction in the number of incidents outside the city centre. However, it must be noted that the data for 2019 is incomplete. The data is limited to incidents prior to June 2019. This is due to missing data from incomplete records. So, once the records are made more up to date, as is observed from 2017 and 2018, the distribution may be more consistant with previous years. 

## Conclusion


Overall, the distribution of single and two vehicle accidents seems to be evenly distributed throughout Calgary. Most of the major roads appear to see the occurance of these accident types. Multi-vehicle incidents tend to be limited more to the large volume roads such as Deerfoot tr. and Glenmore tr. This trend could be explained by the high volume nature of the these streets. With a larger number of vehicles the chance of an accident occurring increases. Adding that roads like Deerfoot and Glenmore are multi-lane streets, you have an increased volume of vehicles concentrated in the same relative space, so, an accident can easily become a multi-vehicle event simply because of the larger volume of vehicles that will travel through the location. These roads also tend to be high speed, which could play a role in the occurance of multi-vehicle events as the reduced reaction time may play as a disadvantage for other drivers. 

For accidents that involve pedestrians, the highest concentration tends to be focused in the city centre. With the high volume of people who travel into the downtown core during the day, it is not surprising that the occurance of pedestrian related accidents is high. The city centre also, sees high levels of foot traffic, so again the chance of an incident occurring is increased. 

The observations of the study appear to agree with most aprehensions Calgarians have when it comes to traffic accident.

One limitation of the dataset is that it does not explicitly reference the inclusion of of cyclist related accidents in the tally. In Calgary, a bike is considered as a vehicle, so, the general use of the term vehicle used to define accidents means it is not possible to distinguish cyclist related accidents from non-cyclist related accidents. It is also not possible to determine whether the city included them in the data.

Going forward, some parameters to include that would be of interest would include the age of the people involved, their sex, whether or not they were impaired (e.g. alcohol or drug use), and the make and model of the vehicle, or simply, a general description of the type of vehicle involved. All these factors have the potential to influence driving habits in Calgary. In relation, these parameters could also affect the overall number of accidents in the city.
There will be more work that can be done on this data set in future such as weekly analysis to see if any meaningfull trend can be discovered, day vs night to find out if driving at night can increase the chance of accidents or morning vs evening analysis to investigate if people coming back from work in the evening could be invoolved in more accidents due to exhastion.
